In [1]:
import pandas as pd
import numpy as np
import os
import time
import random
import gensim
import numpy as np
import os
import torch
from gensim.models import KeyedVectors
from gensim.test.utils import datapath
from matplotlib import pyplot as plt
from matplotlib.pyplot import figure

/home/fatma/.local/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def get_mean_vector(model, words):
    # remove out-of-vocabulary words
    # words: target list words
    # returns average vector for all words in target list
    import numpy as np
    words = [word for word in words if word in model.index_to_key]
    if len(words) >= 1:
        return np.mean(model[words], axis=0)
    else:
        return []

def mdi(mean, gini, weight):
    exp1 =  np.power(mean,weight) 
    exp2 = np.power((1 - gini),1-weight)
    return exp1 * exp2

def get_similarity_Scores(v1,v2):
    from numpy import dot
    from numpy.linalg import norm
    return dot(v1,v2)/(norm(v1)*norm(v2))

def normalize_data(a):
    normalizded_a = []
    amin, amax = min(a), max(a)
    for i in a:
        normalizded_a.append((i-amin) / (amax-amin))
    return normalizded_a
    
def get_similarity_scores_between_target_words_and_attribute_words(model, attribute_words, target_words):
    
    similarity_scores_summary = {}
    words = []
    mean_sim_socres = []

    target_words = [word for word in target_words if word in model.index_to_key]
    attribute_words = [word for word in attribute_words if word in model.index_to_key]
    
    if len(target_words) >= 1 and len(attribute_words) >=1:
        for i in target_words:
            similarity_scores = []
            words.append(i)
            for j in attribute_words:
                cos_sim = get_similarity_Scores(model[i], model[j])
                similarity_scores.append(cos_sim)
            mean_sim_socres.append(np.mean(normalize_data(similarity_scores)))

    similarity_scores_summary["word"] = words
    similarity_scores_summary["mean_sim_score"] = mean_sim_socres
    return similarity_scores_summary

def get_similarity_scores_between_avergare_target_vector_and_attribute_words(model, att_words, target_vector):
    # remove out-of-vocabulary words
    # att_words: wors in the attribute list
    # target_vector: average vector of all words in target group
    similarity_scores_summary = {}
    words_list = []
    similarity_scores = []
    words = [word for word in att_words if word in model.index_to_key]
    print(len(words))
    if len(words) >= 1:
        for i in words:
            print(i)
            words_list.append(i)
            cos_sim = get_similarity_Scores(model[i], target_vector)
            similarity_scores.append(cos_sim)
    similarity_scores_summary["words"] = words_list
    similarity_scores_summary["cos_sim_scores"] = similarity_scores
    similarity_scores_summary["sim_score"] = normalize_data(similarity_scores)

    return similarity_scores_summary


## Read profane words

In [3]:
data_folder = "../../Data/"
embeddings_folder = data_folder+"/word embeddings/"
results_folder = "Results/ethnicity_similarities/U_DESIP/"

In [4]:
profane_words = open(data_folder+"swear_words.txt").read().splitlines()

## read word embeddings

In [6]:
def get_google_news_embeddings(filename,binary=False):
    w2v_model = gensim.models.KeyedVectors.load_word2vec_format(filename, binary=binary)
    return w2v_model


## word similarity

In [ ]:
# convert text to w2v
from gensim.scripts.glove2word2vec import glove2word2vec
GLOVE_DIR = embeddings_folder+"/debiased_word_embedding/U-DeSIP.txt"
w2v_file = embeddings_folder+"/debiased_word_embedding/glove_2_wv_U-DeSIP.txt"
glove2word2vec(GLOVE_DIR, w2v_file)

<ipython-input-7-10448837a7a1>:5: DeprecationWarning: Call to deprecated `glove2word2vec` (KeyedVectors.load_word2vec_format(.., binary=False, no_header=True) loads GLoVE text vectors.).
  glove2word2vec(GLOVE_DIR, w2v_file)


In [14]:
glove_wk_model = KeyedVectors.load_word2vec_format(embeddings_folder+"debiased_word_embedding/glove_2_wv_U-DeSIP.txt", binary=False)

## similar words

In [15]:
glove_wk_model.most_similar("girl")

[('boy', 0.7784117460250854),
 ('woman', 0.709696888923645),
 ('girls', 0.688205897808075),
 ('girlfriend', 0.6096454858779907),
 ('man', 0.5886130332946777),
 ('mother', 0.5770816206932068),
 ('boys', 0.5575633645057678),
 ('her', 0.5498956441879272),
 ('she', 0.5434613227844238),
 ('boyfriend', 0.5309102535247803)]

In [16]:
glove_wk_model.most_similar("queer")

[('lgbtq', 0.6333478093147278),
 ('bisexual', 0.6042945981025696),
 ('transgender', 0.6017271876335144),
 ('lgbt', 0.5433913469314575),
 ('lesbian', 0.53706294298172),
 ('feminist', 0.5166168212890625),
 ('gay', 0.5037734508514404),
 ('feminism', 0.4222022593021393),
 ('transsexual', 0.41001302003860474),
 ('sexuality', 0.4051944315433502)]

In [17]:
glove_wk_model.most_similar("queers")

[('screeching', 0.35115087032318115),
 ('fucked', 0.3464447855949402),
 ('moneen', 0.3313293755054474),
 ('hulud', 0.32383298873901367),
 ('babyshambles', 0.3101003170013428),
 ('epk', 0.30351322889328003),
 ('ponty', 0.30094248056411743),
 ('mulberries', 0.2951379120349884),
 ('weasel', 0.2899836301803589),
 ('deporting', 0.28966259956359863)]

In [18]:
glove_wk_model.most_similar("immigrant")

[('immigrants', 0.7811545729637146),
 ('migrants', 0.579512357711792),
 ('migrant', 0.5698612928390503),
 ('undocumented', 0.5549705624580383),
 ('refugees', 0.5169501304626465),
 ('settlers', 0.5104473829269409),
 ('immigrated', 0.5078169703483582),
 ('emigrants', 0.5035039782524109),
 ('settler', 0.49570679664611816),
 ('impoverished', 0.49029532074928284)]

## minority and 
majority words

In [19]:
harmless_majority_words_clean = ["hetrosexual", "cisgender", "man","male","boy","son","father","husband","brother","white","caucasian",
                                 "european american","european", "norwegian", "canadian", "german", "australian", "english",
                                "french", "american", "swedish", "dutch"]

target_words = ["lesbian","gay","bisexual","transgender","tran","queer",
                "lgbt","lgbtq","homosexual", "woman", "female", "girl","wife","sister","daughter","mother", "non-binary",
               "african", "african american", "asian", "black", "hispanic", "latin", "mexican", "indian", "middle eastern",
                "arab"]

words = harmless_majority_words_clean + target_words

In [20]:
profane_vector = get_mean_vector(glove_wk_model, profane_words)
vec_majority_sim_dict = get_similarity_scores_between_avergare_target_vector_and_attribute_words(glove_wk_model, words, profane_vector)
pd.DataFrame(vec_majority_sim_dict).to_csv(results_folder+"_minority_and_majority_words_sim_to_profane_vector.csv")

44
cisgender
man
male
boy
son
father
husband
brother
white
caucasian
european
norwegian
canadian
german
australian
english
french
american
swedish
dutch
lesbian
gay
bisexual
transgender
tran
queer
lgbt
lgbtq
homosexual
woman
female
girl
wife
sister
daughter
mother
african
asian
black
hispanic
latin
mexican
indian
arab


In [21]:
figure(figsize=(25, 10), dpi=1200)
sorted_index = np.argsort(vec_majority_sim_dict["sim_score"])

x_axis = np.arange(len(vec_majority_sim_dict["words"]))
y_axis = [vec_majority_sim_dict["sim_score"][i] for i in sorted_index]
x_ticks = [vec_majority_sim_dict["words"][i] for i in sorted_index]
plt.bar(x_axis, y_axis)
plt.xticks(x_axis, x_ticks, fontsize=40, fontweight='bold', rotation=90)
plt.ylabel("similarity score", fontsize=40, fontweight='bold')
plt.yticks(np.arange(0.1,1.1,0.1),fontsize=40, fontweight='bold')
plt.savefig(results_folder+"similarity_score_of_minority_and_majority_words_to_profanity_vector.pdf", bbox_inches='tight')